In [2]:
# This Python 3 environment comes with many helpful analytics libraries installed
# It is defined by the kaggle/python Docker image: https://github.com/kaggle/docker-python
# For example, here's several helpful packages to load

import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)

from PIL import Image

# Input data files are available in the read-only "../input/" directory
# For example, running this (by clicking run or pressing Shift+Enter) will list all files under the input directory

import os
for dirname, _, filenames in os.walk('/kaggle/input'):
    for filename in filenames:
        print(os.path.join(dirname, filename))

# You can write up to 20GB to the current directory (/kaggle/working/) that gets preserved as output when you create a version using "Save & Run All" 
# You can also write temporary files to /kaggle/temp/, but they won't be saved outside of the current session

/kaggle/input/haik-24-arabic-sign-language-image-classification/sample_submission.csv
/kaggle/input/haik-24-arabic-sign-language-image-classification/test/test/bomwiebczv.jpg
/kaggle/input/haik-24-arabic-sign-language-image-classification/test/test/egezmdxrzv.jpg
/kaggle/input/haik-24-arabic-sign-language-image-classification/test/test/bhmpblnakx.jpg
/kaggle/input/haik-24-arabic-sign-language-image-classification/test/test/pvsjakxmod.jpg
/kaggle/input/haik-24-arabic-sign-language-image-classification/test/test/sdgasd21 (22).JPG
/kaggle/input/haik-24-arabic-sign-language-image-classification/test/test/unmprikoal.jpg
/kaggle/input/haik-24-arabic-sign-language-image-classification/test/test/htxglmixys.jpg
/kaggle/input/haik-24-arabic-sign-language-image-classification/test/test/tovlevfjur.jpg
/kaggle/input/haik-24-arabic-sign-language-image-classification/test/test/nakifprgbg.jpg
/kaggle/input/haik-24-arabic-sign-language-image-classification/test/test/lmpxrcoqzz.jpg
/kaggle/input/haik-24

In [17]:
import os
import numpy as np
import pandas as pd
from PIL import Image
import cv2
from sklearn.model_selection import train_test_split
from keras.utils import to_categorical

# Define the path to your dataset
dataset_path = '/kaggle/input/haik-24-arabic-sign-language-image-classification/train/train/haik-image claassification'

# Image dimensions
IMG_WIDTH = 64
IMG_HEIGHT = 64

# Create an empty list to store the data
data = []

def to_three_channels(image):
    """Convert a single-channel (grayscale) image to a three-channel (RGB) image."""
    return cv2.cvtColor(image, cv2.COLOR_GRAY2RGB)

# Loop through each folder (each letter)
for letter in os.listdir(dataset_path):
    folder_path = os.path.join(dataset_path, letter)
    if os.path.isdir(folder_path):
        # Loop through each image in the folder
        for image_name in os.listdir(folder_path):
            image_path = os.path.join(folder_path, image_name)
            if image_path.endswith('.jpg') or image_path.endswith('.png'):  # Check for valid image formats
                # Open the image file
                image = Image.open(image_path).convert('L')  # Convert to grayscale
                # Resize the image
                image = image.resize((IMG_WIDTH, IMG_HEIGHT))
                # Convert the image to a numpy array
                image_array = np.array(image)
                # Convert the grayscale image to a 3-channel image
                image_array = to_three_channels(image_array)
                # Append the data
                data.append([image_array, letter])

# Create a DataFrame
df = pd.DataFrame(data, columns=['image', 'label'])

# Check the lengths of the image and label columns
print(f"Number of images: {len(df['image'])}")
print(f"Number of labels: {len(df['label'])}")

# Convert the images to numpy arrays and normalize
X = np.array(df['image'].tolist()) / 255.0
y = df['label'].astype('category').cat.codes  # Convert labels to numeric codes

# Ensure X and y have the same number of samples
assert X.shape[0] == len(y), "Mismatch in the number of samples between X and y."

# One-hot encode the labels
y = to_categorical(y)  # One-hot encode the labels



Number of images: 34168
Number of labels: 34168


In [18]:
label=df.label.unique()
label

array(['kaaaf', 'ra2', 'daal', 'dha2', 'toott', 'zaay', 'taa', 'waaw',
       'thaal', 'thaaa', 'jeeem', 'fa2', 'gaf', 'alif_lam', 'sheeen',
       'yaa', 'haa2', 'alif', 'haa', 'khaaa', 'aeyn', 'saaad', 'ta2',
       'meeem', 'dhaad', 'seeen', 'nuun', 'laaam', 'yaa2', 'ghayn', 'ba2',
       'laa'], dtype=object)

In [19]:
# Function to get image size and number of channels
def get_image_properties(image):
    if len(image.shape) == 2:  # Grayscale image
        return image.shape, 1
    elif len(image.shape) == 3:  # Color image
        return image.shape[:2], image.shape[2]
    else:
        return None

# Initialize a dictionary to store the unique sizes and channel counts
image_sizes = {}
channel_counts = {}

# Iterate through the images and collect their properties
for idx, img in enumerate(df['image']):
    size, channels = get_image_properties(img)
    size_key = str(size)
    
    # Count image sizes
    if size_key in image_sizes:
        image_sizes[size_key] += 1
    else:
        image_sizes[size_key] = 1
    
    # Count channels
    if channels in channel_counts:
        channel_counts[channels] += 1
    else:
        channel_counts[channels] = 1

# Print the results
print("Image sizes and their counts:")
for size, count in image_sizes.items():
    print(f"Size: {size}, Count: {count}")

print("\nNumber of channels and their counts:")
for channels, count in channel_counts.items():
    print(f"Channels: {channels}, Count: {count}")


Image sizes and their counts:
Size: (64, 64), Count: 34168

Number of channels and their counts:
Channels: 3, Count: 34168


# MODEL

In [20]:
from tensorflow.keras.callbacks import LearningRateScheduler

# Define the CNN model
model = Sequential([
    Conv2D(64, (3, 3), activation='relu', input_shape=(IMG_WIDTH, IMG_HEIGHT, 3)),
    MaxPooling2D((2, 2)),
    Conv2D(128, (4, 4), activation='relu'),
    MaxPooling2D((2, 2)),
    Conv2D(224, (6,6), activation='relu'),

    Flatten(),
    Dense(128, activation='relu'),
    Dropout(0.2),
    
    Dense(64, activation='relu'),
    Dense(len(y[0]), activation='softmax')  # Number of classes
])

# Compile the model
model.compile(optimizer=Adam(learning_rate=0.0001*3.17), loss='categorical_crossentropy', metrics=['accuracy'])

# Define a learning rate schedule function
def lr_schedule(epoch, lr):
    if epoch < 8:
        return lr
    else:
        return lr * np.exp(-0.1)

# Create the LearningRateScheduler callback
lr_scheduler = LearningRateScheduler(lr_schedule)


/opt/conda/lib/python3.10/site-packages/keras/src/layers/convolutional/base_conv.py:107: UserWarning: Do not pass an `input_shape`/`input_dim` argument to a layer. When using Sequential models, prefer using an `Input(shape)` object as the first layer in the model instead.
  super().__init__(activity_regularizer=activity_regularizer, **kwargs)


In [21]:
datagen = ImageDataGenerator(
    rotation_range=20,
    fill_mode='nearest'
)

In [22]:


# Train the model
history = model.fit(datagen.flow(X, y, batch_size=32)
, epochs=13, batch_size=32
    , callbacks=[lr_scheduler])

# # Evaluate the model
# test_results = model.evaluate(X, y, verbose=2)

# # Print the results
# #print(f'Test loss: {test_results[0]}')
# #print(f'Test accuracy: {test_results[1]}')
# #print(f'Test F1-score: {test_results[2]}')

# # If you want to get predictions and calculate F1-score manually
# y_pred = model.predict(X_test)
# y_pred_classes = np.argmax(y_pred, axis=1)
# y_true_classes = np.argmax(y_test, axis=1)

# from sklearn.metrics import classification_report, f1_score


# # Calculate and print overall F1-score
# f1 = f1_score(y_true_classes, y_pred_classes, average='macro')
# print(f'Overall F1-score: {f1}')

Epoch 1/13


/opt/conda/lib/python3.10/site-packages/keras/src/trainers/data_adapters/py_dataset_adapter.py:121: UserWarning: Your `PyDataset` class should call `super().__init__(**kwargs)` in its constructor. `**kwargs` can include `workers`, `use_multiprocessing`, `max_queue_size`. Do not pass these arguments to `fit()`, as they will be ignored.
  self._warn_if_super_not_called()


   5/1068 ━━━━━━━━━━━━━━━━━━━━ 35s 34ms/step - accuracy: 0.0408 - loss: 3.4919

I0000 00:00:1722028028.094107     191 device_compiler.h:186] Compiled cluster using XLA!  This line is logged at most once for the lifetime of the process.


1068/1068 ━━━━━━━━━━━━━━━━━━━━ 46s 37ms/step - accuracy: 0.1777 - loss: 2.9002 - learning_rate: 3.1700e-04
Epoch 2/13
1068/1068 ━━━━━━━━━━━━━━━━━━━━ 37s 34ms/step - accuracy: 0.7702 - loss: 0.6736 - learning_rate: 3.1700e-04
Epoch 3/13
1068/1068 ━━━━━━━━━━━━━━━━━━━━ 37s 34ms/step - accuracy: 0.8918 - loss: 0.3216 - learning_rate: 3.1700e-04
Epoch 4/13
1068/1068 ━━━━━━━━━━━━━━━━━━━━ 37s 34ms/step - accuracy: 0.9330 - loss: 0.2063 - learning_rate: 3.1700e-04
Epoch 5/13
1068/1068 ━━━━━━━━━━━━━━━━━━━━ 36s 34ms/step - accuracy: 0.9513 - loss: 0.1496 - learning_rate: 3.1700e-04
Epoch 6/13
1068/1068 ━━━━━━━━━━━━━━━━━━━━ 37s 34ms/step - accuracy: 0.9589 - loss: 0.1288 - learning_rate: 3.1700e-04
Epoch 7/13
1068/1068 ━━━━━━━━━━━━━━━━━━━━ 37s 34ms/step - accuracy: 0.9646 - loss: 0.1089 - learning_rate: 3.1700e-04
Epoch 8/13
1068/1068 ━━━━━━━━━━━━━━━━━━━━ 36s 34ms/step - accuracy: 0.9736 - loss: 0.0825 - learning_rate: 3.1700e-04
Epoch 9/13
1068/1068 ━━━━━━━━━━━━━━━━━━━━ 36s 34ms/step - accuracy:

In [23]:
import tensorflow as tf

# Assuming `model` is your trained model
model.save('base_line_model.keras')

In [ ]:
y_pred[1]

# REsnet

In [ ]:
import cv2
import numpy as np
import pandas as pd

# Assuming df is your DataFrame with 'image' column of shape (None, 64, 64)
# Replace 'df' and 'image_column_name' with your actual DataFrame and column name

# Function to resize and convert to RGB
def preprocess_image(img):
    # Resize image to (240, 240)
    resized_img = cv2.resize(img, (224, 224))
    
    # Convert to RGB if image is grayscale
    if len(resized_img.shape) == 2:
        resized_img = cv2.cvtColor(resized_img, cv2.COLOR_GRAY2RGB)
    
    return resized_img

# Apply preprocessing to all images in the 'image' column
df['image'] = df['image'].apply(preprocess_image)

# Stack images and create final array
images_resized = np.stack(df['image'].to_numpy())

# Now images_resized has shape (none, 240, 240, 3) suitable for ResNet50


In [ ]:
import matplotlib.pyplot as plt

# Extract the image from the dataframe
image = df.image.iloc[1000]

# Plot the image
plt.imshow(image)
plt.axis('off')  # Turn off axis labels
plt.show()


In [ ]:
import tensorflow as tf
from tensorflow.keras.applications import ResNet50
from tensorflow.keras.layers import Dense, GlobalAveragePooling2D
from tensorflow.keras.models import Model
from tensorflow.keras.optimizers import Adam
from sklearn.model_selection import train_test_split
from sklearn.metrics import f1_score
import numpy as np

def to_three_channels(image):
    return cv2.cvtColor(image, cv2.COLOR_GRAY2RGB)

# Apply the conversion to all images in the dataframe
df['image'] = df['image'].apply(to_three_channels)

X = np.array(df['image'].tolist()).reshape(-1, IMG_WIDTH, IMG_HEIGHT, 1) / 255.0


X = np.stack(X)

# Check if lengths of X and y match
print(len(df['image']), len(y))


# Assuming 'images' and 'y' are your data and labels
# Split data into train, validation, and test sets
X_train, X_temp, y_train, y_temp = train_test_split(X, y, test_size=0.3, random_state=42)
X_val, X_test, y_val, y_test = train_test_split(X_temp, y_temp, test_size=0.5, random_state=42)

In [ ]:
model = Sequential()

# Load pre-trained ResNet50 model
base_model =  keras.applications.VGG16(
    include_top=False,
    weights="imagenet",
    input_tensor=None,
    input_shape=(64, 64,1),
    pooling=None,
    classes=1000,
    classifier_activation="softmax",
)

# Add custom layers
model.add(base_model)
model.add(Flatten())
model.add(Dense(512, activation='relu'))
model.add(Dense(y.shape[1], activation='softmax'))

# Freeze base model layers
for layer in base_model.layers:
    layer.trainable = False

# Compile the model
model.compile(optimizer=Adam(learning_rate=0.001), loss='categorical_crossentropy', metrics=['accuracy'])

# Train the model
history = model.fit(
    X_train, y_train,
    batch_size=32,
    epochs=4,
    validation_data=(X_val, y_val)
)

# Make predictions on the test set
y_pred = model.predict(X_test)

# Convert predictions to class labels
y_pred_classes = np.argmax(y_pred, axis=1)
y_test_classes = np.argmax(y_test, axis=1)

# Calculate F1 score
f1 = f1_score(y_test_classes, y_pred_classes, average='weighted')

print(f"F1 Score on test data: {f1:.4f}")

In [ ]:
from sklearn.metrics import confusion_matrix
import seaborn as sns
import matplotlib.pyplot as plt

y_pred_classes = np.argmax(y_pred, axis=1)
y_test_classes = np.argmax(y_test, axis=1)


cm = confusion_matrix(y_test_classes, y_test_classes)
sns.heatmap(cm, annot=True, fmt='d')
plt.show()


In [ ]:
import tensorflow as tf

# Assuming `model` is your trained model
model.save('my_model.keras')

In [ ]:
(y_pred[200])

# submission

In [ ]:
import os

# Define the directory containing the images
image_dir = '/kaggle/input/haik-24-arabic-sign-language-image-classification/test/test'

# List all files in the directory, not just images
all_files = os.listdir(image_dir)

# Count total files in the directory
total_files = len(all_files)
print(f"Total number of files (including non-image files): {total_files}")

# Filter image files with different case extensions
image_files = [f for f in all_files if f.lower().endswith(('.jpg', '.png'))]
print(f"Total number of image files: {len(image_files)}")

# Print the first few file names to check for irregularities
print("Sample files:")
print(all_files[:10])

# List non-image files if any
non_image_files = [f for f in all_files if not f.lower().endswith(('.jpg', '.png'))]
print(f"Total number of non-image files: {len(non_image_files)}")
print("Non-image files:")
print(non_image_files)


In [12]:
import pandas as pd
import numpy as np
import os
from PIL import Image

# Define the directory containing the images
image_dir = '/kaggle/input/haik-24-arabic-sign-language-image-classification/test/test'

# List all image files in the directory
image_files = [f for f in os.listdir(image_dir) if f.endswith('.jpg') or f.endswith('.JPG')]

# Print the total number of image files found
print(f"Total number of image files: {len(image_files)}")

# Create a list to hold the image data
image_data = []

# Read each image file and store the data in the list
for image_file in image_files:
    try:
        image_path = os.path.join(image_dir, image_file)
        image = Image.open(image_path)
        image_array = np.array(image)
        image_data.append([image_file, image_array])
    except Exception as e:
        # Log any errors encountered while processing images
        print(f"Error processing file {image_file}: {e}")

# Create a DataFrame from the image data
dff = pd.DataFrame(image_data, columns=['filename', 'image'])

# Display the DataFrame
dff


Total number of image files: 10797


filename                                              image
0         bomwiebczv.jpg  [[223, 223, 223, 223, 223, 223, 223, 223, 223,...
1         egezmdxrzv.jpg  [[220, 220, 220, 220, 220, 220, 220, 220, 221,...
2         bhmpblnakx.jpg  [[212, 212, 213, 214, 214, 215, 216, 216, 215,...
3         pvsjakxmod.jpg  [[216, 216, 217, 218, 219, 219, 220, 220, 220,...
4      sdgasd21 (22).JPG  [[135, 134, 133, 132, 132, 132, 132, 133, 133,...
...                  ...                                                ...
10792     qckozbivtz.jpg  [[217, 217, 217, 218, 218, 219, 219, 219, 220,...
10793     icbhbduono.jpg  [[230, 230, 230, 231, 231, 232, 232, 232, 233,...
10794     uyiooquouj.jpg  [[222, 222, 222, 222, 222, 222, 222, 222, 221,...
10795    d2wds (333).JPG  [[150, 149, 147, 146, 146, 147, 149, 150, 148,...
10796     rhvjmngoah.jpg  [[214, 214, 215, 215, 215, 216, 216, 216, 217,...

[10797 rows x 2 columns]

In [30]:
dff["Image"]["124wqf12 (63)"]

KeyError: '124wqf12 (63)'

In [ ]:
# Function to get image size and number of channels
def get_image_properties(image):
    if len(image.shape) == 2:  # Grayscale image
        return image.shape, 1
    elif len(image.shape) == 3:  # Color image
        return image.shape[:2], image.shape[2]
    else:
        return None

# Initialize a dictionary to store the unique sizes and channel counts
image_sizes = {}
channel_counts = {}

# Iterate through the images and collect their properties
for idx, img in enumerate(dff['image']):
    size, channels = get_image_properties(img)
    size_key = str(size)
    
    # Count image sizes
    if size_key in image_sizes:
        image_sizes[size_key] += 1
    else:
        image_sizes[size_key] = 1
    
    # Count channels
    if channels in channel_counts:
        channel_counts[channels] += 1
    else:
        channel_counts[channels] = 1

# Print the results
print("Image sizes and their counts:")
for size, count in image_sizes.items():
    print(f"Size: {size}, Count: {count}")

print("\nNumber of channels and their counts:")
for channels, count in channel_counts.items():
    print(f"Channels: {channels}, Count: {count}")


In [5]:
# Check the shape of your data
num_images = len(dff['image'])
image_shape = dff['image'].iloc[0].shape  # Assumes all images have the same shape

# Print out sizes for debugging
print(f"Number of images: {num_images}")
print(f"Image shape: {image_shape}")

# Calculate the expected total number of elements
expected_size = num_images * np.prod(image_shape)
print(f"Expected total size: {expected_size}")

# Check the actual size of your data
actual_size = np.prod(images.shape)
print(f"Actual total size: {actual_size}")


Number of images: 10797
Image shape: (64, 64)
Expected total size: 44224512


NameError: name 'images' is not defined

In [24]:
def preprocess_image(img):
    # Resize image to (240, 240)
    resized_img = cv2.resize(img, (64, 64))
    
    # Convert to RGB if image is grayscale
    if len(resized_img.shape) == 2:
        resized_img = cv2.cvtColor(resized_img, cv2.COLOR_GRAY2RGB)
#     
    return resized_img

# Apply preprocessing to all images in the 'image' column
dff['image'] = dff['image'].apply(preprocess_image)

In [25]:
import numpy as np
import cv2

# Assuming the target shape is (64, 64)
target_shape = (64, 64)

# Function to resize images to the target shape
def resize_image(image, target_shape):
    return cv2.resize(image, target_shape, interpolation=cv2.INTER_AREA)

# Resize all images and stack them
resized_images = [resize_image(image, target_shape) for image in dff['image'].values]
images = np.stack(resized_images)

# The images are already in the shape (number_of_images, 64, 64, 3)
# So we don't need to reshape or convert to RGB

# Normalize images if they are not already normalized
images = images.astype(np.float32) / 255.0

print(images.shape)  # This should print (10797, 64, 64, 3)

(10797, 64, 64, 3)


In [26]:
len(images)

10797

In [27]:
model = tf.keras.models.load_model("/kaggle/working/base_line_model.keras")


# Make predictions
predictions = model.predict(images)
# Convert predictions to class labels
predicted_classes = np.argmax(predictions, axis=1)

# # Add the predictions to the DataFrame
dff['predicted_class'] = predicted_classes
dff['predicted_class']

338/338 ━━━━━━━━━━━━━━━━━━━━ 2s 4ms/step


0        28
1         9
2        25
3        24
4         7
         ..
10792    16
10793     8
10794    17
10795     7
10796    22
Name: predicted_class, Length: 10797, dtype: int64

In [12]:
label

NameError: name 'label' is not defined

In [28]:
# folder_names.sort()

predicted_classes.map(class_mapping)
# Create a mapping from numbers to class labels
class_mapping = {i: label for i, label in enumerate(label)}

# Map the predicted class numbers to class labels
dff['predicted_class_label'] = dff['predicted_class'].map(class_mapping)

# Optionally, print the DataFrame to check the results
(dff[['predicted_class', 'predicted_class_label']].head())

AttributeError: 'numpy.ndarray' object has no attribute 'map'

In [29]:
# Creating a mapping dictionary
mapping_dict = {i: label for i, label in enumerate(label)}

# Applying the mapping to the 'predicted_class' column
dff['predicted_class_label'] = dff['predicted_class'].map(mapping_dict)

# Displaying the DataFrame
(dff)

                filename                                              image  \
0         bomwiebczv.jpg  [[[223, 223, 223], [223, 223, 223], [223, 223,...   
1         egezmdxrzv.jpg  [[[220, 220, 220], [220, 220, 220], [220, 220,...   
2         bhmpblnakx.jpg  [[[212, 212, 212], [212, 212, 212], [213, 213,...   
3         pvsjakxmod.jpg  [[[216, 216, 216], [216, 216, 216], [217, 217,...   
4      sdgasd21 (22).JPG  [[[135, 135, 135], [134, 134, 134], [133, 133,...   
...                  ...                                                ...   
10792     qckozbivtz.jpg  [[[217, 217, 217], [217, 217, 217], [217, 217,...   
10793     icbhbduono.jpg  [[[230, 230, 230], [230, 230, 230], [230, 230,...   
10794     uyiooquouj.jpg  [[[222, 222, 222], [222, 222, 222], [222, 222,...   
10795    d2wds (333).JPG  [[[150, 150, 150], [149, 149, 149], [147, 147,...   
10796     rhvjmngoah.jpg  [[[214, 214, 214], [214, 214, 214], [215, 215,...   

       predicted_class predicted_class_label  
0   

In [30]:
dff.drop(['predicted_class',"image"], axis=1, inplace=True)
dff

filename predicted_class_label
0         bomwiebczv.jpg                  yaa2
1         egezmdxrzv.jpg                 thaaa
2         bhmpblnakx.jpg                 seeen
3         pvsjakxmod.jpg                 dhaad
4      sdgasd21 (22).JPG                  waaw
...                  ...                   ...
10792     qckozbivtz.jpg                  haa2
10793     icbhbduono.jpg                 thaal
10794     uyiooquouj.jpg                  alif
10795    d2wds (333).JPG                  waaw
10796     rhvjmngoah.jpg                   ta2

[10797 rows x 2 columns]

In [35]:
dff = dff.rename(columns={'filename': 'Image', 'predicted_class_label': 'Label'})
dff['Image'] = dff['Image'].str.replace('.JPG', '', case=False)
dff = dff.rename(columns={'predicted_class_label': 'Label'})


dff.to_csv('/kaggle/working/dff13.csv',index=False)


In [31]:

dff['filename'] = [f'image{i+1}.jpg' for i in range(len(dff))]


(dff.head())


filename predicted_class_label
0  image1.jpg                  yaa2
1  image2.jpg                 thaaa
2  image3.jpg                 seeen
3  image4.jpg                 dhaad
4  image5.jpg                  waaw

In [36]:
dff

Image  Label
0          image1   yaa2
1          image2  thaaa
2          image3  seeen
3          image4  dhaad
4          image5   waaw
...           ...    ...
10792  image10793   haa2
10793  image10794  thaal
10794  image10795   alif
10795  image10796   waaw
10796  image10797    ta2

[10797 rows x 2 columns]

In [ ]:
import pandas as pd
df1 = pd.read_csv("/kaggle/input/haik-24-arabic-sign-language-image-classification/sample_submission.csv")
df1

In [ ]:
df1 = df1.drop(df1.index)
df1

In [ ]:
df1["Image"]= dff.Image
df1["Label"]= dff['predicted_class'].map(class_mapping)
df1.to_csv('submission.csv', index = False)

In [ ]:
sample = pd.read_csv('/kaggle/input/icr-identify-age-related-conditions/sample_submission.csv')
sample['class_1'] = rounded_predictions
sample['class_0'] = rounded_class_0 
sample.to_csv('submission.csv', index = False)

In [ ]:
df.to_csv('/kaggle/working/dff5.csv',index=False)

# resnet submission

In [ ]:
import tensorflow as tf

# Load the model from the output directory
model = tf.keras.models.load_model('/kaggle/working/my_model.keras')


In [ ]:
dff['image']

In [ ]:
def preprocess_image(img):
    # Resize image to (240, 240)
    resized_img = cv2.resize(img, (224, 224))
    
    # Convert to RGB if image is grayscale
    if len(resized_img.shape) == 2:
        resized_img = cv2.cvtColor(resized_img, cv2.COLOR_GRAY2RGB)
    
    return resized_img

# Apply preprocessing to all images in the 'image' column
dff['image_res'] = dff['image'].apply(preprocess_image)

In [ ]:
dff['image_res']

In [ ]:
# Function to get image size and number of channels
def get_image_properties(image):
    if len(image.shape) == 2:  # Grayscale image
        return image.shape, 1
    elif len(image.shape) == 3:  # Color image
        return image.shape[:2], image.shape[2]
    else:
        return None

# Initialize a dictionary to store the unique sizes and channel counts
image_sizes = {}
channel_counts = {}

# Iterate through the images and collect their properties
for idx, img in enumerate(dff['image_res']):
    size, channels = get_image_properties(img)
    size_key = str(size)
    
    # Count image sizes
    if size_key in image_sizes:
        image_sizes[size_key] += 1
    else:
        image_sizes[size_key] = 1
    
    # Count channels
    if channels in channel_counts:
        channel_counts[channels] += 1
    else:
        channel_counts[channels] = 1

# Print the results
print("Image sizes and their counts:")
for size, count in image_sizes.items():
    print(f"Size: {size}, Count: {count}")

print("\nNumber of channels and their counts:")
for channels, count in channel_counts.items():
    print(f"Channels: {channels}, Count: {count}")


In [ ]:
# Assuming df is your DataFrame
images = np.stack(dff['image_res'].values)
images = images.reshape(-1, 224, 224, 3)  # Reshape to match model input
images = images / 255.0  # Normalize images if they are not already normalized

In [ ]:
# Make predictions
predictions = model.predict(images)
# Convert predictions to class labels
predicted_classes = np.argmax(predictions, axis=1)

# # Add the predictions to the DataFrame
dff['predicted_class'] = predicted_classes
dff['predicted_class']

In [ ]:
predictions

In [ ]:
predicted_classes

In [38]:
pd.read_csv("/kaggle/input/haik-24-arabic-sign-language-image-classification/sample_submission.csv")

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 10 entries, 0 to 9
Data columns (total 2 columns):
 #   Column  Non-Null Count  Dtype 
---  ------  --------------  ----- 
 0   Image   10 non-null     object
 1   Label   10 non-null     object
dtypes: object(2)
memory usage: 288.0+ bytes


In [37]:
dff.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 10797 entries, 0 to 10796
Data columns (total 2 columns):
 #   Column  Non-Null Count  Dtype 
---  ------  --------------  ----- 
 0   Image   10797 non-null  object
 1   Label   10797 non-null  object
dtypes: object(2)
memory usage: 168.8+ KB
